In [1]:
from datasets import load_dataset, DatasetDict, DownloadMode

zeroth_korean = DatasetDict()

zeroth_korean["train"] = load_dataset("kresnik/zeroth_korean", split="train", download_mode=DownloadMode.REUSE_DATASET_IF_EXISTS)
zeroth_korean["test"] = load_dataset("kresnik/zeroth_korean", split="test", download_mode=DownloadMode.REUSE_DATASET_IF_EXISTS)

print(zeroth_korean)

DatasetDict({
    train: Dataset({
        features: ['file', 'audio', 'text', 'speaker_id', 'chapter_id', 'id'],
        num_rows: 22263
    })
    test: Dataset({
        features: ['file', 'audio', 'text', 'speaker_id', 'chapter_id', 'id'],
        num_rows: 457
    })
})


In [2]:
zeroth_korean = zeroth_korean.remove_columns(["file", "speaker_id", "chapter_id", "id"])

print(zeroth_korean)
# audio랑 text 남기고
# file, speaker_id, chapter_id, id 지우기

DatasetDict({
    train: Dataset({
        features: ['audio', 'text'],
        num_rows: 22263
    })
    test: Dataset({
        features: ['audio', 'text'],
        num_rows: 457
    })
})


In [3]:
from transformers import WhisperFeatureExtractor

feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")

In [4]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-small", language="Korean", task="transcribe")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [5]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Korean", task="transcribe")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [6]:
print(zeroth_korean["train"][0])

{'audio': {'path': '/home/kwon/.cache/huggingface/datasets/downloads/extracted/38285576d48be93072ee02a2cfd2b30b3c4b32eb7022f4c421e5879a9bda428f/train_data_01/003/124/124_003_0009.flac', 'array': array([-3.05175781e-05, -6.10351562e-05, -3.05175781e-05, ...,
       -1.22070312e-04,  1.83105469e-04, -1.22070312e-04]), 'sampling_rate': 16000}, 'text': '이 과정에서 아파트 명의 문제 등으로 말다툼이 벌어졌고 감정이 격해진 송씨가 공구를 침대에 펼쳐놓고 흉기를 아내 가슴에 들이대며 죽여버린다고 협박했다'}


In [7]:

from datasets import Audio

zeroth_korean = zeroth_korean.cast_column("audio", Audio(sampling_rate=16000))

In [8]:
print(zeroth_korean["train"][0])

{'audio': {'path': '/home/kwon/.cache/huggingface/datasets/downloads/extracted/38285576d48be93072ee02a2cfd2b30b3c4b32eb7022f4c421e5879a9bda428f/train_data_01/003/124/124_003_0009.flac', 'array': array([-3.05175781e-05, -6.10351562e-05, -3.05175781e-05, ...,
       -1.22070312e-04,  1.83105469e-04, -1.22070312e-04]), 'sampling_rate': 16000}, 'text': '이 과정에서 아파트 명의 문제 등으로 말다툼이 벌어졌고 감정이 격해진 송씨가 공구를 침대에 펼쳐놓고 흉기를 아내 가슴에 들이대며 죽여버린다고 협박했다'}


In [9]:
from transformers.models.whisper.english_normalizer import BasicTextNormalizer

do_lower_case = False
do_remove_punctuation = False

normalizer = BasicTextNormalizer()

In [10]:
def prepare_dataset(batch):
    # load and (possibly) resample audio data to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array 
    batch["input_features"] = processor.feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]
    # compute input length of audio sample in seconds
    batch["input_length"] = len(audio["array"]) / audio["sampling_rate"]
    
    # optional pre-processing steps
    transcription = batch["text"]
    if do_lower_case:
        transcription = transcription.lower()
    if do_remove_punctuation:
        transcription = normalizer(transcription).strip()
    
    # encode target text to label ids
    batch["labels"] = processor.tokenizer(transcription).input_ids
    return batch

In [11]:
zeroth_korean = zeroth_korean.map(prepare_dataset, remove_columns=zeroth_korean.column_names["train"], num_proc=2)

Map (num_proc=2):   0%|          | 0/22263 [00:00<?, ? examples/s]

Map (num_proc=2):   0%|          | 0/457 [00:00<?, ? examples/s]

In [12]:

max_input_length = 30.0

def is_audio_in_length_range(length):
    return length < max_input_length

In [13]:
zeroth_korean["train"] = zeroth_korean["train"].filter(
    is_audio_in_length_range,
    input_columns=["input_length"],
)

Filter:   0%|          | 0/22263 [00:00<?, ? examples/s]

In [14]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch

In [15]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [16]:
import evaluate

wer_score = evaluate.load("wer")

In [17]:
from evaluate import load
cer_score = evaluate.load("cer")

이게 원본 WER 평가 코드


# evaluate with the 'normalised' WER
do_normalize_eval = True

def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = processor.tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = processor.tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    if do_normalize_eval:
        pred_str = [normalizer(pred) for pred in pred_str]
        label_str = [normalizer(label) for label in label_str]

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

In [18]:
# evaluate with the 'normalised' WER
do_normalize_eval = True

def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = processor.tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = processor.tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    if do_normalize_eval:
        pred_str = [normalizer(pred) for pred in pred_str]
        label_str = [normalizer(label) for label in label_str]

    wer = 100 * wer_score.compute(predictions=pred_str, references=label_str)
    cer = 100 * cer_score.compute(predictions=pred_str, references=label_str)

    return {"wer": wer, "cer": cer}

In [19]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-small")

In [20]:
model.config.forced_decoder_ids = None
model.config.suppress_tokens = []
model.config.use_cache = False

In [21]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./",
    per_device_train_batch_size=16,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=500,
    max_steps=4000,
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="cer",
    greater_is_better=False,
    push_to_hub=True,
)

In [22]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=zeroth_korean["train"],
    eval_dataset=zeroth_korean["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)

In [23]:
processor.save_pretrained(training_args.output_dir)

In [24]:

trainer.train()

  0%|          | 0/4000 [00:00<?, ?it/s]

{'loss': 2.0528, 'learning_rate': 4.4e-07, 'epoch': 0.02}
{'loss': 1.6367, 'learning_rate': 9.400000000000001e-07, 'epoch': 0.04}
{'loss': 1.2439, 'learning_rate': 1.44e-06, 'epoch': 0.05}
{'loss': 0.7302, 'learning_rate': 1.94e-06, 'epoch': 0.07}
{'loss': 0.5361, 'learning_rate': 2.4400000000000004e-06, 'epoch': 0.09}
{'loss': 0.4687, 'learning_rate': 2.9400000000000002e-06, 'epoch': 0.11}
{'loss': 0.4293, 'learning_rate': 3.44e-06, 'epoch': 0.13}
{'loss': 0.3663, 'learning_rate': 3.94e-06, 'epoch': 0.14}
{'loss': 0.3301, 'learning_rate': 4.440000000000001e-06, 'epoch': 0.16}
{'loss': 0.3001, 'learning_rate': 4.94e-06, 'epoch': 0.18}
{'loss': 0.2242, 'learning_rate': 5.4400000000000004e-06, 'epoch': 0.2}
{'loss': 0.2262, 'learning_rate': 5.94e-06, 'epoch': 0.22}
{'loss': 0.2143, 'learning_rate': 6.440000000000001e-06, 'epoch': 0.23}
{'loss': 0.2019, 'learning_rate': 6.9400000000000005e-06, 'epoch': 0.25}
{'loss': 0.1992, 'learning_rate': 7.440000000000001e-06, 'epoch': 0.27}


In [ ]:
kwargs = {
    "dataset_tags": "kresnik/zeroth_korean",
    "dataset": "zeroth_korean",  # a 'pretty' name for the training dataset
    "language": "ko",
    "model_name": "Whisper Small Ko",  # a 'pretty' name for your model
    "finetuned_from": "openai/whisper-small",
    "tasks": "automatic-speech-recognition",
    "tags": "whisper-event",
}

In [ ]:

trainer.push_to_hub(**kwargs)